## Import Libraries - Data

In [22]:
import pandas as pd
import numpy as np
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA

#set the max columns to none
pd.set_option('display.max_columns', None)

In [139]:
# Raw data
size = 'demo'
type = 'train'
articles_path = f'./files/parquet/ebnerd_{size}/articles.parquet'
behaviors_path = f'./files/parquet/ebnerd_{size}/{type}/behaviors.parquet'
history_path = f'./files/parquet/ebnerd_{size}/{type}/history.parquet'
df_articles = pd.read_parquet(articles_path)
df_behaviors = pd.read_parquet(behaviors_path)
df_history = pd.read_parquet(history_path)


# Ready embeddings
#embeddings_path = f'./files/parquet/FacebookAI_xlm_roberta_base/xlm_roberta_base.parquet'
embeddings_path = f'./files/parquet/Ekstra_Bladet_word2vec/document_vector.parquet'
df_embeddings = pd.read_parquet(embeddings_path)

In [4]:
print(df_articles.columns)
print(df_articles.shape)
df_articles.head(5)

Index(['article_id', 'title', 'subtitle', 'last_modified_time', 'premium',
       'body', 'published_time', 'image_ids', 'article_type', 'url',
       'ner_clusters', 'entity_groups', 'topics', 'category', 'subcategory',
       'category_str', 'total_inviews', 'total_pageviews', 'total_read_time',
       'sentiment_score', 'sentiment_label'],
      dtype='object')
(11777, 21)


article_id                                       title  \
0     3037230  Ishockey-spiller: Jeg troede jeg skulle dø   
1     3044020            Prins Harry tvunget til dna-test   
2     3057622                 Rådden kørsel på blå plader   
3     3073151                   Mærsk-arvinger i livsfare   
4     3193383              Skød svigersøn gennem babydyne   

                                            subtitle  last_modified_time  \
0  ISHOCKEY: Ishockey-spilleren Sebastian Harts h... 2023-06-29 06:20:57   
1  Hoffet tvang Prins Harry til at tage dna-test ... 2023-06-29 06:21:16   
2  Kan ikke straffes: Udenlandske diplomater i Da... 2023-06-29 06:21:24   
3  FANGET I FLODBØLGEN: Skibsrederens oldebørn må... 2023-06-29 06:21:38   
4  44-årig kvinde tiltalt for drab på ekssvigersø... 2023-06-29 06:22:57   

   premium                                               body  \
0    False  Ambitionerne om at komme til USA og spille ish...   
1    False  Den britiske tabloidavis The Sun fortsætter me...   
2    False  Slingrende spritkørsel. Grove overtrædelser af...   
3    False  To oldebørn af skibsreder Mærsk McKinney Mølle...   
4    False  En 44-årig mormor blev i dag fremstillet i et ...   

       published_time                    image_ids     article_type  \
0 2003-08-28 08:55:00                         None  article_default   
1 2005-06-29 08:47:00  [3097307, 3097197, 3104927]  article_default   
2 2005-10-10 07:20:00                    [3047102]  article_default   
3 2005-01-04 06:59:00  [3067474, 3067478, 3153705]  article_default   
4 2003-09-15 15:30:00                         None  article_default   

                                                 url           ner_clusters  \
0  https://ekstrabladet.dk/sport/anden_sport/isho...                     []   
1  https://ekstrabladet.dk/underholdning/udlandke...  [Harry, James Hewitt]   
2  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
3  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
4   https://ekstrabladet.dk/krimi/article3193383.ece                     []   

  entity_groups                                             topics  category  \
0            []  [Kriminalitet, Kendt, Sport, Katastrofe, Mindr...       142   
1    [PER, PER]  [Kriminalitet, Kendt, Underholdning, Personfar...       414   
2            []               [Kriminalitet, Transportmiddel, Bil]       118   
3            []  [Erhverv, Privat virksomhed, Livsstil, Familie...       118   
4            []          [Kriminalitet, Personfarlig kriminalitet]       140   

  subcategory   category_str  total_inviews  total_pageviews  total_read_time  \
0  [327, 334]          sport            NaN              NaN              NaN   
1       [432]  underholdning            NaN              NaN              NaN   
2       [133]        nyheder            NaN              NaN              NaN   
3       [133]        nyheder            NaN              NaN              NaN   
4          []          krimi            NaN              NaN              NaN   

   sentiment_score sentiment_label  
0           0.9752        Negative  
1           0.7084        Negative  
2           0.9236        Negative  
3           0.9945        Negative  
4           0.9966        Negative

In [5]:
print(df_behaviors.columns)
print(df_behaviors.shape)
df_behaviors.head(2)

Index(['impression_id', 'article_id', 'impression_time', 'read_time',
       'scroll_percentage', 'device_type', 'article_ids_inview',
       'article_ids_clicked', 'user_id', 'is_sso_user', 'gender', 'postcode',
       'age', 'is_subscriber', 'session_id', 'next_read_time',
       'next_scroll_percentage'],
      dtype='object')
(24724, 17)


impression_id  article_id     impression_time  read_time  \
0          48401         NaN 2023-05-21 21:06:50       21.0   
1         152513   9778745.0 2023-05-24 07:31:26       30.0   

   scroll_percentage  device_type  \
0                NaN            2   
1              100.0            1   

                                  article_ids_inview article_ids_clicked  \
0  [9774516, 9771051, 9770028, 9775402, 9774461, ...           [9759966]   
1  [9778669, 9778736, 9778623, 9089120, 9778661, ...           [9778661]   

   user_id  is_sso_user  gender  postcode  age  is_subscriber  session_id  \
0    22779        False     NaN       NaN  NaN          False          21   
1   150224        False     NaN       NaN  NaN          False         298   

   next_read_time  next_scroll_percentage  
0            16.0                    27.0  
1             2.0                    48.0

In [6]:
print(df_history.columns)
print(df_history.shape)
df_history.head(2)

Index(['user_id', 'impression_time_fixed', 'scroll_percentage_fixed',
       'article_id_fixed', 'read_time_fixed'],
      dtype='object')
(1590, 5)


user_id                              impression_time_fixed  \
0    13538  [2023-04-27T10:17:43.000000, 2023-04-27T10:18:...   
1    58608  [2023-04-27T18:48:09.000000, 2023-04-27T18:48:...   

                             scroll_percentage_fixed  \
0  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...

In [11]:
## Specify the path to your text file
file_path = './files/parquet/predictions.txt'

# Initialize lists to store parsed data
keys = []
values = []

# Open the file in read mode
with open(file_path, 'r') as file:
    # Read each line in the file
    for line in file:
        # Strip any leading/trailing whitespace characters
        line = line.strip()
        
        # Extract the key (number before the '[' character)
        key_start = line.find(' ')
        key = int(line[:key_start])
        
        # Extract the value (list of integers inside the brackets)
        value_str = line[key_start:]
        value = [int(num) for num in value_str.strip()[1:-1].split(',')]  # Extract and convert to list of integers
        
        # Append key and value to lists
        keys.append(key)
        values.append(value)

# Create a DataFrame from the lists of keys and values
df = pd.DataFrame({'Key': keys, 'Value': values})



In [4]:
df

Key                                              Value
0         6451339                        [8, 1, 6, 7, 4, 2, 9, 5, 3]
1         6451363                           [5, 4, 3, 7, 6, 8, 1, 2]
2         6451382                                    [1, 5, 3, 4, 2]
3         6451383                [7, 6, 8, 9, 3, 4, 2, 11, 10, 1, 5]
4         6451385                              [5, 3, 2, 4, 7, 6, 1]
...           ...                                                ...
13536705        0  [120, 49, 179, 32, 30, 42, 155, 50, 45, 234, 9...
13536706        0  [248, 62, 36, 2, 152, 199, 241, 235, 155, 160,...
13536707        0  [163, 77, 143, 232, 69, 16, 27, 119, 186, 166,...
13536708        0  [113, 233, 67, 105, 130, 8, 100, 173, 158, 28,...
13536709        0  [142, 17, 248, 67, 201, 159, 163, 219, 22, 40,...

[13536710 rows x 2 columns]

## I will create two tables with embeddings, one will come from df_articles and the other from the other two dfs joined. I will try firstly the embeddings that are provided and more specificaly the word2vec embeddings, in order to create a proof of concept. After that if it is needed i will begin from the raw data to build the embeddings from scratch.

## Pre process df_articles

In [56]:
df_embeddings

article_id                                    document_vector
0          3000022  [0.06542388, -0.047424573, 0.06384871, -0.0014...
1          3000063  [0.028815078, -0.00016637295, 0.055056807, 0.0...
2          3000613  [0.037971217, 0.03392251, 0.027297212, 0.01708...
3          3000700  [0.04652399, 0.0029133065, 0.06280604, -0.0051...
4          3000840  [0.014736942, 0.024067875, 0.0051865038, 0.041...
...            ...                                                ...
125536     9803505  [0.029624538, -0.039833125, -0.03009815, 0.005...
125537     9803510  [-0.0284717, -0.035652492, 0.027552828, -0.018...
125538     9803525  [0.039465133, 0.00079695834, 0.062067263, 0.08...
125539     9803560  [0.0049191406, 0.01373551, 0.020911952, 0.0108...
125540     9803607  [0.0005135782, -0.046943206, 0.054680478, 0.02...

[125541 rows x 2 columns]

In [57]:
df_articles.head()

article_id                                       title  \
0     3037230  Ishockey-spiller: Jeg troede jeg skulle dø   
1     3044020            Prins Harry tvunget til dna-test   
2     3057622                 Rådden kørsel på blå plader   
3     3073151                   Mærsk-arvinger i livsfare   
4     3193383              Skød svigersøn gennem babydyne   

                                            subtitle  last_modified_time  \
0  ISHOCKEY: Ishockey-spilleren Sebastian Harts h... 2023-06-29 06:20:57   
1  Hoffet tvang Prins Harry til at tage dna-test ... 2023-06-29 06:21:16   
2  Kan ikke straffes: Udenlandske diplomater i Da... 2023-06-29 06:21:24   
3  FANGET I FLODBØLGEN: Skibsrederens oldebørn må... 2023-06-29 06:21:38   
4  44-årig kvinde tiltalt for drab på ekssvigersø... 2023-06-29 06:22:57   

   premium                                               body  \
0    False  Ambitionerne om at komme til USA og spille ish...   
1    False  Den britiske tabloidavis The Sun fortsætter me...   
2    False  Slingrende spritkørsel. Grove overtrædelser af...   
3    False  To oldebørn af skibsreder Mærsk McKinney Mølle...   
4    False  En 44-årig mormor blev i dag fremstillet i et ...   

       published_time                    image_ids     article_type  \
0 2003-08-28 08:55:00                         None  article_default   
1 2005-06-29 08:47:00  [3097307, 3097197, 3104927]  article_default   
2 2005-10-10 07:20:00                    [3047102]  article_default   
3 2005-01-04 06:59:00  [3067474, 3067478, 3153705]  article_default   
4 2003-09-15 15:30:00                         None  article_default   

                                                 url           ner_clusters  \
0  https://ekstrabladet.dk/sport/anden_sport/isho...                     []   
1  https://ekstrabladet.dk/underholdning/udlandke...  [Harry, James Hewitt]   
2  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
3  https://ekstrabladet.dk/nyheder/samfund/articl...                     []   
4   https://ekstrabladet.dk/krimi/article3193383.ece                     []   

  entity_groups                                             topics  category  \
0            []  [Kriminalitet, Kendt, Sport, Katastrofe, Mindr...       142   
1    [PER, PER]  [Kriminalitet, Kendt, Underholdning, Personfar...       414   
2            []               [Kriminalitet, Transportmiddel, Bil]       118   
3            []  [Erhverv, Privat virksomhed, Livsstil, Familie...       118   
4            []          [Kriminalitet, Personfarlig kriminalitet]       140   

  subcategory   category_str  total_inviews  total_pageviews  total_read_time  \
0  [327, 334]          sport            NaN              NaN              NaN   
1       [432]  underholdning            NaN              NaN              NaN   
2       [133]        nyheder            NaN              NaN              NaN   
3       [133]        nyheder            NaN              NaN              NaN   
4          []          krimi            NaN              NaN              NaN   

   sentiment_score sentiment_label  
0           0.9752        Negative  
1           0.7084        Negative  
2           0.9236        Negative  
3           0.9945        Negative  
4           0.9966        Negative

In [58]:
df_articles.isnull().sum()

article_id               0
title                    0
subtitle                 0
last_modified_time       0
premium                  0
body                     0
published_time           0
image_ids              937
article_type             0
url                      0
ner_clusters             0
entity_groups            0
topics                   0
category                 0
subcategory              0
category_str             0
total_inviews         4271
total_pageviews       4271
total_read_time       4271
sentiment_score          0
sentiment_label          0
dtype: int64

In [59]:
#df_articles = df_articles.drop(["image_ids", "total_inviews", "total_pageviews", "total_read_time", "last_modified_time", "published_time", "url"], axis= 1)

df_articles = df_articles[["article_id"]]

In [60]:
df_articles.head()

article_id
0     3037230
1     3044020
2     3057622
3     3073151
4     3193383

In [61]:
df_articles_embeddings = pd.merge(df_articles, df_embeddings, on="article_id") 

In [62]:
df_articles_embeddings.head()

article_id                                    document_vector
0     3037230  [0.017898837, -0.012223162, 0.0117029, 0.03572...
1     3044020  [0.041870505, 0.002982251, 0.07588886, -0.0031...
2     3057622  [0.03602814, -0.004919843, -0.005812604, 0.015...
3     3073151  [0.039754465, -0.014155321, 0.044064052, 0.040...
4     3193383  [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [65]:
df_articles_embeddings = df_articles_embeddings.set_index('article_id')

In [66]:
df_articles_embeddings.head()

document_vector
article_id                                                   
3037230     [0.017898837, -0.012223162, 0.0117029, 0.03572...
3044020     [0.041870505, 0.002982251, 0.07588886, -0.0031...
3057622     [0.03602814, -0.004919843, -0.005812604, 0.015...
3073151     [0.039754465, -0.014155321, 0.044064052, 0.040...
3193383     [0.014357477, -0.07686433, 0.07009871, 0.02835...

In [67]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
columns_to_process = ['document_vector']

# Unpack lists in each specified column
for col in columns_to_process:
    df_articles_embeddings = unpack_lists(df_articles_embeddings, col)

In [69]:
df_articles_embeddings.drop('document_vector', axis=1, inplace=True)

In [71]:
df_articles_embeddings.shape

(11777, 300)

## Pre process df_behaviors and df_history

In [143]:
# df_behaviors.isnull().sum()
# df_behaviors = df_behaviors.drop(["impression_id","impression_time", "scroll_percentage", "gender", "postcode","age","article_id", "next_read_time", "next_scroll_percentage"], axis=1)
# df_behaviors.isnull().sum()
# df_users = pd.merge(df_behaviors, df_history, on="user_id") 




In [140]:
df_users = df_history.copy()

In [141]:
df_users =df_users.drop(["impression_time_fixed"], axis=1)

In [142]:
df_users.head()

user_id                            scroll_percentage_fixed  \
0    13538  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1    58608  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   
2    95507  [60.0, 100.0, 100.0, 21.0, 29.0, 67.0, 49.0, 5...   
3   106588  [24.0, 57.0, 100.0, nan, nan, 100.0, 100.0, 73...   
4   617963  [100.0, 100.0, nan, 46.0, 23.0, 19.0, 61.0, 70...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   
2  [9739035, 9738646, 9634967, 9738902, 9735495, ...   
3  [9738292, 9738216, 9737266, 9737556, 9737657, ...   
4  [9739035, 9739088, 9738902, 9738968, 9738760, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...  
2  [18.0, 29.0, 51.0, 12.0, 10.0, 10.0, 13.0, 24....  
3  [9.0, 15.0, 42.0, 9.0, 3.0, 58.0, 26.0, 214.0,...  
4  [45.0, 29.0, 116.0, 26.0, 34.0, 42.0, 58.0, 59...

In [144]:
# for col in ["is_sso_user", "is_subscriber"]:
#     df_users[col] = df_users[col].replace({False: 0, True: 1})

In [145]:
# def has_na(x):
#     if np.nan in x:
#         return True
#     else:
#         return False

In [146]:
# for col in ["article_ids_inview", "scroll_percentage_fixed", "read_time_fixed","article_id_fixed", "article_ids_clicked"]:
#     df_users[col+"_nans"] = df_users[col].map(has_na)
#     print(df_users[col+"_nans"].unique())

## Nans do not exist inside the lists

In [147]:
# df_users = df_users.drop(["article_ids_inview_nans", "read_time_fixed_nans", "scroll_percentage_fixed_nans", "article_id_fixed_nans", "article_ids_clicked_nans"], axis=1)

In [148]:
df_users.head()

user_id                            scroll_percentage_fixed  \
0    13538  [100.0, 35.0, 100.0, 24.0, 100.0, 23.0, 100.0,...   
1    58608  [37.0, 61.0, 100.0, 100.0, 55.0, 100.0, 100.0,...   
2    95507  [60.0, 100.0, 100.0, 21.0, 29.0, 67.0, 49.0, 5...   
3   106588  [24.0, 57.0, 100.0, nan, nan, 100.0, 100.0, 73...   
4   617963  [100.0, 100.0, nan, 46.0, 23.0, 19.0, 61.0, 70...   

                                    article_id_fixed  \
0  [9738663, 9738569, 9738663, 9738490, 9738663, ...   
1  [9739362, 9739179, 9738567, 9739344, 9739202, ...   
2  [9739035, 9738646, 9634967, 9738902, 9735495, ...   
3  [9738292, 9738216, 9737266, 9737556, 9737657, ...   
4  [9739035, 9739088, 9738902, 9738968, 9738760, ...   

                                     read_time_fixed  
0  [17.0, 12.0, 4.0, 5.0, 4.0, 9.0, 5.0, 46.0, 11...  
1  [2.0, 24.0, 72.0, 65.0, 11.0, 4.0, 101.0, 0.0,...  
2  [18.0, 29.0, 51.0, 12.0, 10.0, 10.0, 13.0, 24....  
3  [9.0, 15.0, 42.0, 9.0, 3.0, 58.0, 26.0, 214.0,...  
4  [45.0, 29.0, 116.0, 26.0, 34.0, 42.0, 58.0, 59...

## Unpack list in columns

In [149]:
def unpack_lists(df, column_name):
    # Create new columns by unpacking lists in the specified column
    unpacked_cols = pd.DataFrame(df[column_name].tolist(), index=df.index)
    # Rename the columns with a prefix based on the original column name
    unpacked_cols = unpacked_cols.add_prefix(column_name + '_')
    # Concatenate the unpacked columns back to the original DataFrame
    df = pd.concat([df, unpacked_cols], axis=1)
    return df

# Specify which columns to process
# columns_to_process = ['article_ids_inview', 'article_ids_clicked', 'scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']
columns_to_process = ['scroll_percentage_fixed', 'article_id_fixed', 'read_time_fixed']

# Unpack lists in each specified column
for col in columns_to_process:
    df_users = unpack_lists(df_users, col)


In [151]:
df_users = df_users.drop(columns_to_process, axis=1)

In [152]:
df_users = df_users.set_index('user_id')

In [153]:
df_users

scroll_percentage_fixed_0  scroll_percentage_fixed_1  \
user_id                                                         
13538                        100.0                       35.0   
58608                         37.0                       61.0   
95507                         60.0                      100.0   
106588                        24.0                       57.0   
617963                       100.0                      100.0   
...                            ...                        ...   
1122370                      100.0                      100.0   
1718049                       53.0                      100.0   
1178033                        NaN                       98.0   
395912                       100.0                      100.0   
2539047                       46.0                      100.0   

         scroll_percentage_fixed_2  scroll_percentage_fixed_3  \
user_id                                                         
13538                        100.0                       24.0   
58608                        100.0                      100.0   
95507                        100.0                       21.0   
106588                       100.0                        NaN   
617963                         NaN                       46.0   
...                            ...                        ...   
1122370                      100.0                      100.0   
1718049                       24.0                      100.0   
1178033                       92.0                       30.0   
395912                       100.0                       33.0   
2539047                       40.0                      100.0   

         scroll_percentage_fixed_4  scroll_percentage_fixed_5  \
user_id                                                         
13538                        100.0                       23.0   
58608                         55.0                      100.0   
95507                         29.0                       67.0   
106588                         NaN                      100.0   
617963                        23.0                       19.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       83.0                       28.0   
1178033                       35.0                        9.0   
395912                         NaN                        NaN   
2539047                      100.0                      100.0   

         scroll_percentage_fixed_6  scroll_percentage_fixed_7  \
user_id                                                         
13538                        100.0                      100.0   
58608                        100.0                        NaN   
95507                         49.0                       54.0   
106588                       100.0                       73.0   
617963                        61.0                       70.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       37.0                       40.0   
1178033                       34.0                       58.0   
395912                         NaN                        NaN   
2539047                       28.0                      100.0   

         scroll_percentage_fixed_8  scroll_percentage_fixed_9  \
user_id                                                         
13538                        100.0                       26.0   
58608                         61.0                      100.0   
95507                         25.0                       19.0   
106588                        26.0                       30.0   
617963                        64.0                       72.0   
...                            ...                        ...   
1122370                        NaN                        NaN   
1718049                       22.0      

In [154]:
def create_pca_embeddings(df, columns, n_components):
    # Fill NaN values with a default value (-999)
    df_filled = df[columns].fillna(-999)
    
    # Initialize PCA model
    pca = PCA(n_components=n_components)
    
    # Fit PCA on the numerical data
    embeddings = pca.fit_transform(df_filled.values)
    
    # Create a new DataFrame to store PCA embeddings with the same index as the original DataFrame
    embeddings_df = pd.DataFrame(embeddings, index=df.index)
    
    # Rename columns of the embeddings DataFrame
    embeddings_df.columns = [f'pca_embedding_{i}' for i in range(n_components)]
    
    return embeddings_df

In [155]:
# Specify columns to apply embeddings
columns_for_embeddings = list(df_users.columns)

# Apply PCA embeddings to ID columns
df_users_embeddings = create_pca_embeddings(df_users, columns_for_embeddings, n_components=300)

In [156]:
df_users_embeddings

pca_embedding_0  pca_embedding_1  pca_embedding_2  pca_embedding_3  \
user_id                                                                       
13538       1.524437e+08     7.024936e+07     2.424417e+07    -4.800035e+06   
58608       6.188810e+05    -4.392026e+07     2.797433e+07     5.439820e+06   
95507       1.054429e+08    -8.282102e+06    -4.236038e+07    -2.434165e+07   
106588     -6.160550e+05    -4.314132e+07     2.848665e+07     4.230237e+06   
617963      6.778455e+07    -4.299940e+07    -3.036714e+07     1.598942e+07   
...                  ...              ...              ...              ...   
1122370    -6.293004e+07     3.137580e+07    -2.105634e+07     1.663342e+07   
1718049    -6.276366e+07     3.107744e+07    -2.061967e+07     1.602400e+07   
1178033    -6.276408e+07     3.107821e+07    -2.062078e+07     1.602556e+07   
395912     -6.293004e+07     3.137579e+07    -2.105636e+07     1.663344e+07   
2539047    -6.215212e+07     2.997349e+07    -1.903626e+07     1.384987e+07   

         pca_embedding_4  pca_embedding_5  pca_embedding_6  pca_embedding_7  \
user_id                                                                       
13538      -1.913102e+07    -2.804426e+07    -2.275579e+07    -1.847000e+07   
58608      -2.084014e+07     9.453188e+06     7.442964e+06    -1.142627e+07   
95507       3.451099e+06     2.239256e+07     1.253899e+07    -3.892277e+06   
106588     -2.045310e+07     1.024573e+07     6.415888e+06    -1.154919e+07   
617963      2.340479e+07    -3.429266e+06    -1.649835e+07    -3.407469e+06   
...                  ...              ...              ...              ...   
1122370    -1.279853e+07     9.319078e+06    -9.918904e+06     7.158301e+06   
1718049    -1.208053e+07     8.556942e+06    -8.838233e+06     6.158039e+06   
1178033    -1.208237e+07     8.558904e+06    -8.841042e+06     6.160611e+06   
395912     -1.279856e+07     9.319102e+06    -9.918917e+06     7.158339e+06   
2539047    -9.565259e+06     5.940312e+06    -5.186841e+06     2.899692e+06   

         pca_embedding_8  pca_embedding_9  pca_embedding_10  pca_embedding_11  \
user_id                                                                         
13538      -4.554227e+06     7.486377e+06      1.202081e+07      1.674945e+07   
58608       4.813609e+06     5.422490e+06     -8.498500e+06     -1.245145e+05   
95507      -1.419121e+07    -4.671329e+06      5.457152e+06      9.468693e+06   
106588      5.830200e+06     4.527233e+06     -8.758907e+06      1.076175e+06   
617963      1.400487e+07     2.413570e+06     -1.005895e+07     -6.375482e+06   
...                  ...              ...               ...               ...   
1122370    -6.213981e+06     6.707649e+06     -7.065240e+06      5.260484e+06   
1718049    -5.123833e+06     5.279987e+06     -5.314119e+06      3.703353e+06   
1178033    -5.126716e+06     5.283721e+06     -5.318610e+06      3.707328e+06   
395912     -6.213941e+06     6.707699e+06     -7.065286e+06      5.260517e+06   
2539047    -1.672613e+06     8.593113e+05     -3.942732e+04     -8.176298e+05   

         pca_embedding_12  pca_embedding_13  pca_embedding_14  \
user_id                                                         
13538        1.107631e+07     -2.135642e+05     -8.219258e+06   
58608        4.404852e+06     -6.931038e+06     -8.720222e+05   
95507       -2.400122e+04     -8.869927e+06     -1.162876e+07   
106588       3.500167e+06     -7.580919e+06      2.939209e+05   
617963       8.710007e+06      6.359307e+06     -3.412634e+06   
...                   ...               ...               ...   
1122370     -4.766219e+06      5.708506e+06     -3.550131e+06   
1718049     -3.215844e+06      3.466178e+06     -1.939324e+06   
1178033     -3.219813e+06      3.471947e+06     -1.943501e+06   
395912      -4.766243e+06      5.708557e+06     -3.550115e+06   
2539047      1.173970e+06     -2.348325e+06      2.023347e+06   

         pca_embedding_15  pca_embedding_16  pca_embe

## Create user-article matrix

## Compute Interaction Matrix|:
##### Compute the recommendation score for each item i for the user u using the learned embeddings.
##### The recommendation score can be calculated as the dot product (similarity) between the user embedding u_emb and the item embedding v_i for each item i.
#### Score(𝑢,𝑖)=𝑢_𝑒𝑚𝑏^𝑇 × 𝑣𝑖

#### Where:
#### - u_emb: User embedding vector for user u.
#### - v_i: Item embedding vector for item i.
#### -  ^T: Transpose operation.
#### -  \times: Dot product.

In [157]:
# Compute user-article interaction matrix X using matrix multiplication
X = np.dot(df_users_embeddings, df_articles_embeddings.T)

# X is now a matrix of shape (N_users, N_articles) containing combined embeddings

In [158]:
X_df = pd.DataFrame(X, index = df_users_embeddings.index.values, columns = df_articles_embeddings.index.values)

In [159]:
X_df.head()

3037230       3044020       3057622       3073151       3193383  \
13538  -1.993529e+06  1.018807e+07  4.574092e+06  5.702941e+06 -3.338242e+06   
58608  -3.452506e+05 -5.605572e+05  2.638119e+05 -7.973650e+05  3.732664e+06   
95507  -1.439205e+06 -9.433509e+04  1.653503e+06 -2.588502e+06 -5.823619e+06   
106588 -4.972741e+05  8.943281e+04  2.518587e+05 -9.858440e+05  4.048768e+06   
617963  2.634798e+06  1.390665e+06  4.351105e+06  5.014257e+06  7.408562e+06   

             3196611       3200325       3200913       3209311       3209357  \
13538  -7.681365e+06  3.065306e+05 -2.553973e+06 -2.831826e+06 -2.580988e+06   
58608   3.273408e+06  1.820627e+06  3.872150e+05  3.014872e+06  2.174876e+06   
95507  -8.355584e+06 -5.953613e+06 -6.216683e+06 -6.621853e+06 -5.028146e+06   
106588  3.612613e+06  1.656878e+06  5.154150e+05  3.238228e+06  2.193592e+06   
617963  3.115835e+06  5.159930e+06  3.901874e+06  6.316829e+06  3.703627e+06   

             3223114       3251664       3971783       3977720       3983641  \
13538  -1.019468e+05 -7.765736e+05  5.049812e+06  4.541917e+06 -2.342402e+06   
58608   8.133243e+05  3.971650e+05 -1.143885e+06  1.116008e+06  2.995258e+05   
95507  -2.578784e+06  3.293285e+06  1.965253e+06  3.290160e+05 -6.258478e+06   
106588  2.186325e+05  8.936919e+04 -1.610284e+06  4.359261e+05  5.074604e+05   
617963  3.970904e+06  4.262550e+06  2.574111e+06  6.750684e+06  9.417016e+05   

             3987418       3988589       3993395       3994264       3997229  \
13538  -7.704352e+05 -3.973790e+06  5.156650e+06 -2.305287e+06 -7.717391e+05   
58608   1.225453e+06  1.102034e+06  1.163845e+06 -1.240020e+04  4.040736e+06   
95507  -4.714710e+06 -9.975008e+06 -8.750790e+05 -5.513668e+06 -5.143532e+06   
106588  1.199781e+06  1.127741e+06  1.347918e+06 -2.703338e+04  3.486667e+06   
617963  5.185430e+05 -1.366389e+06  5.737295e+06  4.021333e+06  1.371463e+06   

             3997233       3998680       4000567       4000823       4003163  \
13538  -5.123278e+06 -3.911132e+06  3.213875e+06 -2.272405e+06 -1.424499e+06   
58608   3.432561e+06 -5.187695e+05  1.387269e+06 -7.622863e+05  3.189641e+06   
95507  -6.403311e+06 -5.690736e+05 -1.350662e+06 -9.140254e+05 -5.318509e+06   
106588  3.462265e+06 -7.880087e+05  8.994810e+05 -1.123301e+06  3.190523e+06   
617963  5.113904e+06 -1.787660e+05  3.957518e+06  2.084003e+06  4.305815e+06   

             4003362       4003431       4003926       4007811       4008213  \
13538  -2.136573e+06  1.464636e+06  3.674887e+06  6.297378e+06 -1.686896e+06   
58608   2.416870e+06  9.484344e+05 -7.418840e+05  5.864024e+05  1.678067e+06   
95507  -5.909521e+06 -8.720202e+05  6.883134e+06 -3.895099e+06 -3.903455e+06   
106588  2.290385e+06  7.192887e+05 -1.224901e+06  1.816617e+05  9.849218e+05   
617963  3.064939e+06  4.054416e+06  1.617897e+06  3.184972e+06  1.957741e+06   

             4009177       4014381       4021392       4024289       4024449  \
13538  -2.206757e+06 -3.472287e+06  6.267421e+06  5.210136e+06  8.037289e+06   
58608   2.707580e+06 -8.210853e+04 -2.365986e+06  2.054141e+04 -1.105995e+04   
95507  -5.666603e+06 -4.224381e+06  1.226546e+06  1.526590e+06 -1.977928e+06   
106588  2.613667e+06 -3.004908e+05 -2.087064e+06  2.974558e+05 -2.333028e+05   
617963  4.875155e+06  2.112895e+06  3.165562e+06  2.416544e+06  3.561836e+06   

             4026960       4035059       4035605       4040731       4040737  \
13538   2.307228e+06 -1.783681e+05  2.432593e+06  2.007373e+06  1.777681e+06   
58608   1.457263e+06 -2.989111e+06  5.078756e+05  1.854463e+06  5.069371e+05   
95507  -6.308832e+06 -2.452884e+05  4.612206e+06 -3.402221e+06 -4.557283e+06   
106588  1.305491e+06 -3.624301e+06  5.759777e+05  2.057656e+06  5.853941e+05   
617963  4.934261e+06  2.435998e+06  4.722472e+06  6.972602e+06  7.026388e+06   

             4043121       4044042       4045439       4048845       4050800  \
13538   3.519702e+06  1.817985e+06 -2.453369e+06  7.285818e+06  3.584216e+04   
58608

#### Singular Value Decomposition (SVD): SVD is used to decompose the user-movie interaction matrix X into three matrices: U (user embeddings), sigma (singular values), and Vt (transposed movie embeddings).
#### Number of Latent Factors (k): Specify the number of latent factors (embedding dimensions) to use in the matrix factorization.
#### Reconstruction of Embeddings:
##### - Compute sigma_diag, a diagonal matrix containing the singular values.
##### - Compute U_train (user embeddings) by multiplying U with the square root of sigma_diag.
##### - Compute V_train (movie embeddings) by multiplying the square root of sigma_diag with Vt.

In [185]:
from scipy.sparse.linalg import svds

# Perform Singular Value Decomposition (SVD) on the user-movie interaction matrix X
# X should be a dense matrix
k = 300  # Number of latent factors (embedding dimensions)

U, sigma, Vt = svds(X_df.values, k=k)  # Perform SVD, obtaining U, sigma, Vt

# Diagonalize the singular values sigma to create a diagonal matrix
sigma_diag = np.diag(sigma)

# Reconstruct the user and movie embeddings
U_train = np.dot(U, np.sqrt(sigma_diag))  # User embeddings
V_train = np.dot(np.sqrt(sigma_diag), Vt)  # Movie embeddings

In [189]:
U_train_df =  pd.DataFrame(U_train, index = X_df.index.values)
V_train_df =  pd.DataFrame(V_train.T, index = X_df.columns.values)

## Recommendation Process
##### To generate recommendations for a specific user, follow these steps:

#### a) Retrieve User's Recommendations
##### Select User: Choose the target user for whom you want to generate recommendations.
#### b) Extract User's Interaction Scores
##### User's Row in X: Retrieve the row corresponding to the selected user from the matrix X. Let's denote this row as X_user.
#### c) Rank Items by Interaction Scores
##### Sort Interaction Scores: Sort the values in the X_user row in descending order. Each value represents the interaction score between the user (selected) and a specific item.
#### d) Recommend Top-N Items
##### Top-N Recommendations: Select the top-N items with the highest interaction scores from the sorted X_user row. These items are recommended to the user based on their predicted preferences.

## Load Validation Data

In [160]:
# Raw validation data
size = 'demo'
type = 'validation'
behaviors_validation_path = f'./files/parquet/ebnerd_{size}/{type}/behaviors.parquet'
history_validation_path = f'./files/parquet/ebnerd_{size}/{type}/history.parquet'
df_behaviors_val = pd.read_parquet(behaviors_validation_path)
df_history_val = pd.read_parquet(history_validation_path)

In [206]:
df_history_val['user_id']

0        750497
1         22779
2        373598
3        383378
4        411733
         ...   
1557     626090
1558    1143249
1559     109970
1560     330156
1561    2385386
Name: user_id, Length: 1562, dtype: uint32

In [210]:
recommendation_scores.keys()

dict_keys([750497, 22779, 373598, 383378, 411733, 782168, 795659, 890209, 891255, 1703304, 19181, 22895, 28327, 40054])

In [208]:
# Initialize an empty dictionary to store recommendation scores for each user
recommendation_scores = {}

# Iterate over each user in the validation dataset
for user_id in df_history_val['user_id'].unique():
    # Retrieve user embedding for the current user
    user_embedding = U_train_df.loc[user_id,:] # Assuming user_id corresponds to row index in U_train

    # Compute recommendation scores for all items using dot product with item embeddings
    scores = np.dot(V_train_df, user_embedding)

    # Sort items based on scores in descending order
    sorted_indices = np.argsort(scores)[::-1]  # Sort indices in descending order
    sorted_items = [item_id for item_id in sorted_indices]  # Convert indices to item IDs

    # Store sorted recommended item IDs for the user in recommendation_scores dictionary
    recommendation_scores[user_id] = sorted_items

KeyError: 121010

In [180]:
user_id = df_history_val['user_id'][1]

In [202]:
U_train_df.loc[user_id,:]

0       -69.020107
1       -60.837970
2        -9.421284
3       176.639753
4      -251.857660
          ...     
295    2373.354755
296    2979.866793
297   -2256.674462
298   -3041.127770
299   -5435.788198
Name: 22779, Length: 300, dtype: float64

In [203]:
recommendation_scores = {}
# Retrieve user embedding for the current user
user_embedding = U_train_df.loc[user_id,:]  # Assuming user_id corresponds to row index in U_train

# Compute recommendation scores for all items using dot product with item embeddings
scores = np.dot(V_train_df, user_embedding)

# Sort items based on scores in descending order
sorted_indices = np.argsort(scores)[::-1]  # Sort indices in descending order
sorted_items = [item_id for item_id in sorted_indices]  # Convert indices to item IDs

# Store sorted recommended item IDs for the user in recommendation_scores dictionary
recommendation_scores[user_id] = sorted_items

In [204]:
top_n_recommendations = {}
top_n = 10  # Number of top recommendations to generate

for user_id, recommended_items in recommendation_scores.items():
    top_n_recommendations[user_id] = recommended_items[:top_n]

In [201]:
top_n_recommendations

{22779: [5867, 9824, 8933, 4421, 5989, 5091, 3593, 2702, 5130, 9622]}

#### If a user_id from the validation set does not exist in the U_train matrix (user embeddings obtained from matrix factorization), it means that the user was not present in the training data used for matrix factorization. In this case, you have several options to handle such scenarios:

#### Fallback Strategy:
##### Use a fallback strategy such as recommending popular or trending items to users not present in U_train.
##### For example, you can recommend the most popular items across all users or based on recent trends if a user is new and their preferences are unknown.
#### User Cold Start Handling:
##### Implement a specific handling mechanism for new or cold-start users (users with no historical interactions in the training data).
##### For cold-start users, consider hybrid recommendation approaches or content-based recommendation methods using user profile information (if available).
#### Default Recommendations:
##### Provide default recommendations or a diverse set of items to users without historical data.
##### This can help engage users initially and gather feedback to improve personalized recommendations over time.
#### Skip Recommendation:
##### Skip generating recommendations for users not present in U_train if they represent a small proportion of the validation dataset.
##### Log or handle these cases separately for further analysis or improvement in the recommendation system.